In [8]:
import requests
import time
from collections import deque
import csv

API_KEY = 'eaf9d33a0591ed52e9b0fbda64013b87'
BASE_URL = 'http://ws.audioscrobbler.com/2.0/'

def get_artist_info(artist_name):
    params = {
        'method': 'artist.getinfo',
        'artist': artist_name,
        'api_key': API_KEY,
        'format': 'json'
    }

    response = requests.get(BASE_URL, params=params).json()
    artist_data = response['artist']

    # Extracting required data
    simplified_data = {
        'name': artist_data['name'],
        'playable': artist_data.get('streamable', '0') == '1',  # Check if it's streamable
        'ontour': artist_data.get('ontour', '0') == '1',  # Check if the artist is on tour
        'stats': {
            'listeners': artist_data['stats']['listeners'],
            'playcount': artist_data['stats']['playcount']
        },
        'similar_artists': [artist['name'] for artist in artist_data['similar']['artist']],
        'tags': [tag['name'] for tag in artist_data['tags']['tag']]
    }

    return simplified_data

def get_artist_albums(artist_name):
    params = {
        'method': 'artist.gettopalbums',
        'artist': artist_name,
        'api_key': API_KEY,
        'format': 'json',
        'limit': 10  # Limiting to 10 top albums for brevity, you can adjust as needed
    }

    response = requests.get(BASE_URL, params=params).json()
    albums = []
    for album in response['topalbums']['album']:
        albums.append(album['name'])
    
    return albums

def bfs(starting_artist, depth_limit=10):
    visited = set()
    queue = deque([(starting_artist, 0)])  # artist_name, depth
    artist_list = []
    max_num = 10000
    cnt = 0
    while queue:
        artist_name, depth = queue.popleft()
        if artist_name in visited:
            continue
        visited.add(artist_name)

        try:
            artist_info = get_artist_info(artist_name)
            artist_list.append(artist_info)
            print(f"Artist Info for {artist_name}:")
            for key, value in artist_info.items():
                print(f"{key.capitalize()}: {value}")
            
            artist_albums = get_artist_albums(artist_name)
            artist_info['albums'] = artist_albums  # 添加这一行
            print(f"Albums for {artist_name}:")
            print(artist_albums)

            print("\n")
        except Exception as e:
            print(f"Error fetching info for {artist_name}: {e}")
            continue

        if depth < depth_limit:
            for similar_artist in artist_info['similar_artists']:
                queue.append((similar_artist, depth+1))
#         time.sleep(0.05)  # Avoid making rapid API calls
        cnt = cnt + 1
        print(cnt)
        if cnt > max_num:
            break

    return artist_list

def save_to_csv(data_list, filename='artist_data.csv'):
    with open(filename, mode='w', newline='', encoding='utf-8') as file:
        fieldnames = ['name', 'playable', 'ontour', 'listeners', 'playcount', 'similar_artists', 'tags', 'albums']
        writer = csv.DictWriter(file, fieldnames=fieldnames)
        writer.writeheader()

        for artist_data in data_list:
            row = {
                'name': artist_data['name'],
                'playable': artist_data['playable'],
                'ontour': artist_data['ontour'],
                'listeners': artist_data['stats']['listeners'],
                'playcount': artist_data['stats']['playcount'],
                'similar_artists': ', '.join(artist_data['similar_artists']),
                'tags': ', '.join(artist_data['tags']),
                # 注意：这里您需要先为 artist_data 添加 albums 信息。目前的代码中并没有添加这部分。
                'albums': ', '.join(artist_data.get('albums', []))
            }
            writer.writerow(row)



if __name__ == '__main__':
    artist_data_list = bfs('Coldplay')
    save_to_csv(artist_data_list)

Artist Info for Coldplay:
Name: Coldplay
Playable: False
Ontour: True
Stats: {'listeners': '7101975', 'playcount': '537662628'}
Similar_artists: ['Keane', 'Imagine Dragons', 'Travis', 'OneRepublic', 'Snow Patrol']
Tags: ['rock', 'alternative', 'britpop', 'alternative rock', 'indie']
Albums for Coldplay:
['Parachutes', 'A Rush of Blood to the Head', 'Viva la Vida or Death and All His Friends', 'X&Y', 'Mylo Xyloto', 'X & Y', 'A Head Full Of Dreams', 'Ghost Stories', 'Viva la Vida', 'Music of the Spheres']


1
Artist Info for Keane:
Name: Keane
Playable: False
Ontour: False
Stats: {'listeners': '3057130', 'playcount': '82268903'}
Similar_artists: ['Tom Chaplin', 'Mt. Desolation', 'Travis', 'Thirteen Senses', 'Coldplay']
Tags: ['britpop', 'indie', 'alternative', 'british', 'rock']
Albums for Keane:
['Hopes and Fears', 'Under the Iron Sea', 'Perfect Symmetry', 'Hopes And Fears (deluxe edition)', 'Strangeland', 'Somewhere Only We Know', 'Night Train', 'The Best Of Keane (Deluxe Edition)', 'T

Albums for The Script:
['The Script', 'Science & Faith', '#3 Deluxe Version', 'No Sound Without Silence', '#3', 'We Cry', "The Man Who Can't Be Moved", 'Freedom Child', 'Superheroes', 'Hall of Fame']


16
Artist Info for Maroon 5:
Name: Maroon 5
Playable: False
Ontour: False
Stats: {'listeners': '4962279', 'playcount': '175481177'}
Similar_artists: ['OneRepublic', 'Adam Levine', 'The Script', 'Train', 'Bruno Mars']
Tags: ['rock', 'pop', 'pop rock', 'alternative', 'alternative rock']
Albums for Maroon 5:
['Songs About Jane', "It Won't Be Soon Before Long", 'V', 'Songs About Jane: 10th Anniversary Edition', 'Overexposed', 'Hands All Over', 'Overexposed Track By Track', 'Red Pill Blues (Deluxe)', 'V (Deluxe)', 'Hands All Over (Revised International Standard version)']


17
Artist Info for Athlete:
Name: Athlete
Playable: False
Ontour: False
Stats: {'listeners': '893920', 'playcount': '12857595'}
Similar_artists: ['Thirteen Senses', 'Feeder', 'Embrace', 'Starsailor', 'Doves']
Tags: ['indie

Albums for The Verve:
['Urban Hymns', 'Urban Hymns (Remastered 2016)', 'This Is Music: The Singles 92-98', 'Forth', 'A Northern Soul', 'Urban Hymns (Deluxe / Remastered 2016)', 'A Storm In Heaven', 'Homecoming (disc 2)', 'Bitter Sweet Symphony', 'Love Is Noise']


31
Artist Info for Liam Gallagher:
Name: Liam Gallagher
Playable: False
Ontour: False
Stats: {'listeners': '292486', 'playcount': '8133498'}
Similar_artists: ['Beady Eye', 'Oasis', "Noel Gallagher's High Flying Birds", 'Noel Gallagher', 'Richard Ashcroft']
Tags: ['britpop', 'rock', 'british', 'seen live', 'god']
Albums for Liam Gallagher:
['As You Were (Deluxe Edition)', 'Why Me? Why Not. (Deluxe Edition)', 'Wall Of Glass', 'Spotify Singles', "Everything's Electric", 'C’MON YOU KNOW (Deluxe Edition)', "All You're Dreaming Of", "For What It's Worth", 'Shockwave', 'Acoustic Sessions']


32
Artist Info for Noel Gallagher's High Flying Birds:
Name: Noel Gallagher's High Flying Birds
Playable: False
Ontour: True
Stats: {'listeners

Artist Info for Augustana:
Name: Augustana
Playable: False
Ontour: True
Stats: {'listeners': '710496', 'playcount': '13221370'}
Similar_artists: ['Five for Fighting', "Jack's Mannequin", 'The Fray', 'Lifehouse', 'Something Corporate']
Tags: ['alternative', 'piano rock', 'indie', 'rock', 'alternative rock']
Albums for Augustana:
['All The Stars and Boulevards', "Can't Love, Can't Hurt", 'Midwest Skies and Sleepless Mondays', 'Augustana', 'Sweet and Low', "Can't Love, Can't Hurt EP", 'Life Imitating Life', 'All The Stars And Boulevards (Advance)', 'Augustana Pre-Release', 'Mayfield EP']


46
Artist Info for Five for Fighting:
Name: Five for Fighting
Playable: False
Ontour: False
Stats: {'listeners': '866967', 'playcount': '9563774'}
Similar_artists: ['Howie Day', 'Edwin McCain', 'Rob Thomas', 'Vertical Horizon', 'Augustana']
Tags: ['alternative', 'rock', 'singer-songwriter', 'alternative rock', 'pop']
Albums for Five for Fighting:
['The Battle For Everything', 'America Town', 'Two Lights

Artist Info for Patty Griffin:
Name: Patty Griffin
Playable: False
Ontour: False
Stats: {'listeners': '335100', 'playcount': '4596308'}
Similar_artists: ['Eliza Gilkyson', 'Shawn Colvin', 'Mary Gauthier', 'Greg Brown', 'Tift Merritt']
Tags: ['folk', 'singer-songwriter', 'female vocalists', 'Alt-country', 'americana']
Albums for Patty Griffin:
['Children Running Through', 'Impossible Dream', '1000 Kisses', 'Living With Ghosts', 'Flaming Red', 'American Kid', 'Downtown Church', 'A Kiss In Time', 'Servant of Love', 'Patty Griffin']


60
Artist Info for Guillemots:
Name: Guillemots
Playable: False
Ontour: False
Stats: {'listeners': '412439', 'playcount': '6173416'}
Similar_artists: ['Fyfe Dangerfield', 'Delays', 'The Boxer Rebellion', 'Doves', 'Elbow']
Tags: ['indie', 'seen live', 'indie rock', 'british', 'alternative']
Albums for Guillemots:
['Through The Windowpane', 'Red', 'From the Cliffs', 'I Saw Such Things in My Sleep EP', 'Walk the River', 'Trains to Brazil', 'Hello Land!', 'Made-U

...

Artist Info for Meatbodies:
Name: Meatbodies
Playable: False
Ontour: False
Stats: {'listeners': '58248', 'playcount': '761013'}
Similar_artists: ['Fuzz', 'Ty Segall', 'Wand', 'Frankie and the Witch Fingers', 'Thee Oh Sees']
Tags: ['Garage Rock', 'Psychedelic Rock', 'Stoner Rock', 'seen live', 'psychedelic']
Albums for Meatbodies:
['Meatbodies', 'Alice', '333', 'Valley Girl', 'Wahoo', '(null)', 'Reach for the Sunn', 'The Hero', 'Cancer', 'KEXP Song of the Day']


8791
Artist Info for Levitation Room:
Name: Levitation Room
Playable: False
Ontour: False
Stats: {'listeners': '167196', 'playcount': '1583929'}
Similar_artists: ['Sugar Candy Mountain', 'Moses Gunn Collective', 'Mystic Braves', 'The Holydrug Couple', 'The Murlocs']
Tags: ['Garage Rock', 'psychedelic', 'Psychedelic Rock', 'indie rock', 'indie']
Albums for Levitation Room:
['Minds Of Our Own', 'Ethos', 'Warmth of the Sun', 'Headspace', 'Pienso En Ti', 'Quarantine', 'Scene for an Exit', 'Mr. Polydactyl Cat', 'Ooh Child', '(null)'

Albums for Naked City:
['Torture Garden', 'Naked City Live Vol. 1 - Knitting Factory 1989', 'Radio', 'Grand Guignol', 'Naked City', 'Heretic, Jeux des Dames Cruelles', 'Absinthe', "Leng Tch'e", "Live in Quebec '88", '(null)']


8806
Artist Info for Port O'Brien:
Name: Port O'Brien
Playable: False
Ontour: False
Stats: {'listeners': '178982', 'playcount': '2472772'}
Similar_artists: ['Loch Lomond', 'Cloud Cult', 'The Dodos', 'The Rural Alberta Advantage', 'Two Gallants']
Tags: ['seen live', 'folk', 'indie', 'indie folk', 'indie rock']
Albums for Port O'Brien:
['All We Could Do Was Sing', 'The Wind and the Swell', 'Threadbare', 'I Woke Up Today', 'All We Could Do Was Sing (Ref. Master w/ Bonus tracks)', 'Indie/Rock Playlist: October (2008)', 'Indie/Rock Playlist: July (2008)', "Be Yourself: A Tribute To Graham Nash's Songs For Beginners", "Blalock's Indie/Rock Playlist: April (2009)", "Blalock's Indie/Rock Playlist: October (2009)"]


8807
Artist Info for scruffpuppie:
Name: scruffpuppie


Albums for Swearin':
["Swearin'", 'Surfing Strange', 'Fall Into the Sun', 'What a Dump', 'Grow into a Ghost', 'Untitled (LA)', 'Dust In The Gold Sack', 'Future Hell', "Swearin' on Audiotree Live", '(null)']


8822
Artist Info for Chumped:
Name: Chumped
Playable: False
Ontour: False
Stats: {'listeners': '28929', 'playcount': '600825'}
Similar_artists: ['Lemuria', 'P.S. Eliot', 'Mixtapes', 'Muncie Girls', 'All Dogs']
Tags: ['pop punk', 'seen live', 'punk', 'Pop-punk', 'emo']
Albums for Chumped:
['Chumped', 'Teenage Retirement', "That's The Thing Is Like", '(null)', 'Chumped - EP', "That's The Thing Is Like...", 'Not the One', 'Faux Real II', "That's the Thing Is Like - Single", 'MIX 1']


8823
Artist Info for Lemuria:
Name: Lemuria
Playable: False
Ontour: True
Stats: {'listeners': '100158', 'playcount': '4423955'}
Similar_artists: ['Chumped', 'The Ergs!', 'P.S. Eliot', 'Cayetana', 'Spraynard']
Tags: ['pop punk', 'folk metal', 'indie', 'seen live', 'black metal']
Albums for Lemuria:
['Get

Albums for Robert Pollard:
['From a Compound Eye', 'Robert Pollard Is Off to Business', 'Waved Out', 'Speak Kindly of Your Volunteer Fire Department (2019 Remaster)', 'Not in My Airforce', 'Space City Kicks', 'Mouseman Cloud', 'The Crawling Distance', 'Fiction Man', 'Lord of the Birdcage']


8838
Artist Info for Tobin Sprout:
Name: Tobin Sprout
Playable: False
Ontour: False
Stats: {'listeners': '27381', 'playcount': '432427'}
Similar_artists: ['Robert Pollard', 'Guided by Voices', 'Silkworm', 'Portastatic', 'Superchunk']
Tags: ['Lo-Fi', 'indie rock', 'indie', 'rock', 'seen live']
Albums for Tobin Sprout:
['Moonflower Plastic', 'Empty Horses', 'Carnival Boy', 'Moonflower Plastic (Welcome to My Wigwam)', 'The Universe and Me', "Let's Welcome the Circus People", 'Lost Planets & Phantom Voices', 'Live At the Horseshoe Tavern', 'Demos and Outtakes', 'Moonflower Plastic (Welcome To My Wig Wam)']


8839
Artist Info for Lou Barlow:
Name: Lou Barlow
Playable: False
Ontour: False
Stats: {'listen

Artist Info for Laura Jane Grace & the Devouring Mothers:
Name: Laura Jane Grace & the Devouring Mothers
Playable: False
Ontour: False
Stats: {'listeners': '19639', 'playcount': '329436'}
Similar_artists: ['Laura Jane Grace', 'Against Me!', 'Tom Gabel', 'Rent Strike', 'Bad Astronaut']
Tags: ['punk', 'folk punk', 'rock', 'american', 'punk rock']
Albums for Laura Jane Grace & the Devouring Mothers:
['Bought to Rot', 'Apocalypse Now (& Later)', 'The Airplane Song', 'Reality Bites', "Save Stereogum: An '00s Covers Comp", '(null)', 'Bought to Rot [Explicit]', 'Good Music to Avert the Collapse of American Democracy', 'Apocalypse Now (& Later) [Explicit]', 'Pandemophenia']


8853
Artist Info for Johnny Reid:
Name: Johnny Reid
Playable: False
Ontour: False
Stats: {'listeners': '13179', 'playcount': '233254'}
Similar_artists: ['Jason Michael Carroll', 'Ashleigh Dallas', 'Gord Bamford', 'B.W. Stevenson', 'Aubrie Sellers']
Tags: ['country', 'Canadian', 'male country', 'modern country', 'johnny']
